# Processing VCF file using Hail

In [2]:
%scala
displayHTML(frameIt("https://en.wikipedia.org/wiki/Variant_Call_Format",500))

Fallback link for browsers that, unlikely, don't support frames

## This Notebook is based on the tutorial [Analyzing 1000 Genomes with Spark and Hail](https://docs.databricks.com/spark/latest/training/1000-genomes.html)

## Cluster setup

On the Databricks interface, click the `Clusters` icon on the left sidebar and then `+Create Cluster`. In the Databricks cluster creation dialog, click `Show advanced settings` at bottom and then on the `Spark` tab, and paste the text below into the `Spark config` box.

```
spark.hadoop.io.compression.codecs org.apache.hadoop.io.compress.DefaultCodec,is.hail.io.compress.BGzipCodec,org.apache.hadoop.io.compress.GzipCodec
spark.sql.files.openCostInBytes 1099511627776
spark.sql.files.maxPartitionBytes 1099511627776
spark.hadoop.mapreduce.input.fileinputformat.split.minsize 1099511627776
spark.hadoop.parquet.block.size 1099511627776```
Start the cluster and attach this notebook to it by clicking on your cluster name in menu `Detached` at the top left of this workbook. Now you're ready to Hail!

In [5]:
from hail import *
hc = HailContext(sc)

In [6]:
import pandas as pd
import numpy as np
from math import log, isnan
import seaborn

In [7]:
display(dbutils.fs.ls("/databricks-datasets/hail/data-001"))

path name size dbfs:/databricks-datasets/hail/data-001/1kg_annotations.txt 1kg_annotations.txt 22784 dbfs:/databricks-datasets/hail/data-001/1kg_sample.vcf.bgz 1kg_sample.vcf.bgz 39767725 dbfs:/databricks-datasets/hail/data-001/purcell5k.interval_list purcell5k.interval_list 192078

## Download the data

In [9]:
vcf_path = '/databricks-datasets/hail/data-001/1kg_sample.vcf.bgz'
annotation_path = '/databricks-datasets/hail/data-001/1kg_annotations.txt'
purcell_5k_path = '/databricks-datasets/hail/data-001/purcell5k.interval_list'

In [10]:
display(dbutils.fs.ls("/databricks-datasets/hail/data-001"))

path name size dbfs:/databricks-datasets/hail/data-001/1kg_annotations.txt 1kg_annotations.txt 22784 dbfs:/databricks-datasets/hail/data-001/1kg_sample.vcf.bgz 1kg_sample.vcf.bgz 39767725 dbfs:/databricks-datasets/hail/data-001/purcell5k.interval_list purcell5k.interval_list 192078

In [11]:
vds = hc.import_vcf(vcf_path)

This method produced a [VariantDataset](https://hail.is/hail/hail.VariantDataset.html), Hail's primary representation of genomic data. Following that link to Hail's python API documentation will let you see the myriad methods it offers.

In [13]:
%scala 
displayHTML(frameIt("https://hail.is/docs/0.1/overview.html#variant-dataset-vds", 500))

Fallback link for browsers that, unlikely, don't support frames

In [14]:
vds = vds.annotate_samples_table(annotation_path,
                                 root='sa.myAnnot',
                                 sample_expr='Sample',
                                 config=TextTableConfig(impute=True))

Use VaraintDataset function count() to get a sense of number of samples, genotypes and variants. However, any aggregate function usually runs pretty slow because of data collection cost

In [16]:
vds.count()

Out[ 114 ]: {u'nSamples': 710, u'nVariants': 10961L, u'nGenotypes': 7782310L}

In [17]:
vds.num_samples

Out[ 80 ]: 710

In [18]:
vds.count_variants()

Out[ 115 ]: 10961L

In [19]:
dir(vds)

Out[ 45 ]: 
['__class__',
 '__delattr__',
 '__dict__',
 '__doc__',
 '__format__',
 '__getattribute__',
 '__hash__',
 '__init__',
 '__module__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 '_global_schema',
 '_globals',
 '_jvds',
 '_num_samples',
 '_sa_schema',
 '_sample_annotations',
 '_sample_ids',
 '_typecheck',
 '_va_schema',
 'aggregate_by_key',
 'aggregate_intervals',
 'annotate_alleles_expr',
 'annotate_global_list',
 'annotate_global_py',
 'annotate_global_table',
 'annotate_samples_expr',
 'annotate_samples_fam',
 'annotate_samples_list',
 'annotate_samples_table',
 'annotate_samples_vds',
 'annotate_variants_bed',
 'annotate_variants_expr',
 'annotate_variants_intervals',
 'annotate_variants_keytable',
 'annotate_variants_loci',
 'annotate_variants_table',
 'annotate_variants_vds',
 'cache',
 'concordance',
 'count',
 'count_variants',
 'deduplicate',
 'downsample_variants',
 'export_gen',
 'export_genotypes',
 'export_plink',
 'export_samples',
 'export_variants',
 'export_variants_cass',
 'export_variants_solr',
 'export_vcf',
 'file_version',
 'filter_alleles',
 'filter_genotypes',
 'filter_multi',
 'filter_samples_all',
 'filter_samples_expr',
 'filter_samples_list',
 'filter_variants_all',
 'filter_variants_expr',
 'filter_variants_intervals',
 'filter_variants_list',
 'global_schema',
 'globals',
 'grm',
 'hardcalls',
 'hc',
 'ibd',
 'impute_sex',
 'is_dosage',
 'join',
 'linreg',
 'lmmreg',
 'logreg',
 'make_keytable',
 'mendel_errors',
 'min_rep',
 'num_partitions',
 'num_samples',
 'pca',
 'persist',
 'query_samples',
 'query_samples_typed',
 'query_variants',
 'query_variants_typed',
 'rename_samples',
 'repartition',
 'same',
 'sample_annotations',
 'sample_ids',
 'sample_qc',
 'sample_schema',
 'samples_keytable',
 'sparkinfo',
 'split_multi',
 'tdt',
 'variant_qc',
 'variant_schema',
 'variants_keytable',
 'vep',
 'was_split',
 'write']

## Start exploring

If the Boolean parameter `genotypes` is set to `True`, the overall call rate across all genotypes is computed as well:

In [22]:
vds.count(genotypes=True)

Out[ 116 ]: {u'nGenotypes': 7782310L, u'nVariants': 10961L, u'nSamples': 710, u'nCalled': 7689777L, u'callRate': 98.81098285727502}

So the call rate before any QC filtering is about 99%.

Let's print variant and sample schemas

In [24]:
print(vds.variant_schema)

Struct {
 rsid: String,
 qual: Double,
 filters: Set[String],
 pass: Boolean,
 info: Struct {
 AC: Array[Int],
 AF: Array[Double],
 AN: Int,
 BaseQRankSum: Double,
 ClippingRankSum: Double,
 DP: Int,
 DS: Boolean,
 FS: Double,
 HaplotypeScore: Double,
 InbreedingCoeff: Double,
 MLEAC: Array[Int],
 MLEAF: Array[Double],
 MQ: Double,
 MQ0: Int,
 MQRankSum: Double,
 QD: Double,
 ReadPosRankSum: Double,
 set: String
 }
}

In [25]:
print(vds.sample_schema)

Struct {
 myAnnot: Struct {
 Sample: String,
 Population: String,
 SuperPopulation: String,
 isFemale: Boolean,
 PurpleHair: Boolean,
 CaffeineConsumption: Double
 }
}

Now it's easy to count samples by population using the [counter](https://hail.is/expr_lang.html#counter) aggregator:

In [27]:
counter = vds.query_samples('samples.map(s => sa.myAnnot.Population).counter()')[0]
for x in counter:
    print('population %s found %s times' % (x.key, x.count))

population ESN found 32 times
population GIH found 30 times
population CHS found 30 times
population PEL found 30 times
population PUR found 24 times
population BEB found 27 times
population MXL found 17 times
population GWD found 39 times
population ACB found 33 times
population PJL found 30 times
population GBR found 33 times
population IBS found 22 times
population YRI found 24 times
population LWK found 28 times
population KHV found 25 times
population FIN found 23 times
population ASW found 19 times
population JPT found 35 times
population CEU found 31 times
population CLM found 25 times
population STU found 22 times
population TSI found 31 times
population CHB found 33 times
population CDX found 26 times
population ITU found 23 times
population MSL found 18 times

##VCF file contains many annotations scores that define the quality of genotypes and variants, which allows genotypes and varaints filtering

In [29]:
%scala
displayHTML(frameIt("https://en.wikipedia.org/wiki/Phred_quality_score",500))

Fallback link for browsers that, unlikely, don't support frames

##Let's first filter genotypes based on genotype quality (GQ) and read coverage (DP).

In [31]:
filter_condition_gDP_gGQ = 'g.dp >= 5 && g.gq >= 20'
vds_gDP_gGQ = vds.filter_genotypes(filter_condition_gDP_gGQ)

In [32]:
vds_gDP_gGQ.count(genotypes=True)

Out[ 126 ]: {u'nGenotypes': 7782310L, u'nVariants': 10961L, u'nSamples': 710, u'nCalled': 7683439L, u'callRate': 98.72954174274733}

Now the call rate is about 50%, so nearly 35% of genotypes failed the filter. Filtering out a genotype is equivalent to setting the genotype call to missing.

Having removed suspect genotypes, let's next remove variants with low call rate and then calculate summary statistics per sample with the [sample_qc](https://hail.is/hail/hail.VariantDataset.html#hail.VariantDataset.sample_qc) method.

In [34]:
vds_gDP_gGQ_vCR = (vds_gDP_gGQ
    .filter_variants_expr('gs.fraction(g => g.isCalled) >= 0.40')
    .sample_qc())

Check how many variants retained after filtering.

In [36]:
vds_gDP_gGQ_vCR.count(genotypes=True)

Out[ 91 ]: {u'nGenotypes': 6936700L, u'nVariants': 9770L, u'nSamples': 710, u'nCalled': 3939258L, u'callRate': 56.78864589790535}

### Filter samples

The call rate for each variant is calculated using the `fraction` [aggregable](https://hail.is/expr_lang.html#aggregables) on the genotypes `gs`. [sample_qc](https://hail.is/hail/hail.VariantDataset.html#hail.VariantDataset.sample_qc) adds a number of statistics to sample annotations:

In [39]:
print(vds_gDP_gGQ_vCR.sample_schema)

Struct {
 myAnnot: Struct {
 Sample: String,
 Population: String,
 SuperPopulation: String,
 isFemale: Boolean,
 PurpleHair: Boolean,
 CaffeineConsumption: Double
 },
 qc: Struct {
 callRate: Double,
 nCalled: Int,
 nNotCalled: Int,
 nHomRef: Int,
 nHet: Int,
 nHomVar: Int,
 nSNP: Int,
 nInsertion: Int,
 nDeletion: Int,
 nSingleton: Int,
 nTransition: Int,
 nTransversion: Int,
 dpMean: Double,
 dpStDev: Double,
 gqMean: Double,
 gqStDev: Double,
 nNonRef: Int,
 rTiTv: Double,
 rHetHomVar: Double,
 rInsertionDeletion: Double
 }
}

We examine the samples' callRate and readdepth to determine the criteria for filtering

In [41]:
sampleqc_table = vds_gDP_gGQ_vCR.samples_keytable().to_dataframe()

new_column_name_list= list(map(lambda x: x.replace(".", "_"), sampleqc_table.columns))
sampleqc_table = sampleqc_table.toDF(*new_column_name_list)

In [42]:
display(sampleqc_table)

s sa_myAnnot_Sample sa_myAnnot_Population sa_myAnnot_SuperPopulation sa_myAnnot_isFemale sa_myAnnot_PurpleHair sa_myAnnot_CaffeineConsumption sa_qc_callRate sa_qc_nCalled sa_qc_nNotCalled sa_qc_nHomRef sa_qc_nHet sa_qc_nHomVar sa_qc_nSNP sa_qc_nInsertion sa_qc_nDeletion sa_qc_nSingleton sa_qc_nTransition sa_qc_nTransversion sa_qc_dpMean sa_qc_dpStDev sa_qc_gqMean sa_qc_gqStDev sa_qc_nNonRef sa_qc_rTiTv sa_qc_rHetHomVar sa_qc_rInsertionDeletion HG00096 HG00096 GBR EUR false false 77.0 0.2749232343909928 2686 7084 1130 1248 308 1864 0 0 1 1524 340 7.4586746090841425 1.8291623838959317 45.90655249441547 28.46876215640281 1556 4.482352941176471 4.0519480519480515 null HG00100 HG00100 GBR EUR true false 59.0 0.9616171954964176 9395 375 5081 2779 1535 5849 0 0 2 4762 1087 13.224374667376209 3.712169739189841 55.6111761575305 27.065478772644916 4314 4.380864765409384 1.8104234527687297 null HG00105 HG00105 GBR EUR false false 77.0 0.5797338792221085 5664 4106 2793 2024 847 3718 0 0 0 2993 725 8.650600282485852 2.2771253327175165 44.382591807909634 27.390137262730732 2871 4.128275862068966 2.3896103896103895 null HG00114 HG00114 GBR EUR false true 72.0 0.14943705220061412 1460 8310 509 776 175 1126 0 0 0 924 202 6.986301369863015 1.6055823053687388 43.37945205479454 25.086450301723687 951 4.574257425742574 4.434285714285714 null HG00115 HG00115 GBR EUR false true 71.0 0.6856704196519959 6699 3071 3479 2218 1002 4222 0 0 1 3451 771 9.22779519331246 2.5460202117218307 44.704433497536925 26.70956053033648 3220 4.476005188067445 2.2135728542914173 null HG00116 HG00116 GBR EUR false false 71.0 0.25220061412487205 2464 7306 1065 1075 324 1723 0 0 0 1403 320 7.394074675324675 1.7025517387131073 40.977678571428584 23.627226861323056 1399 4.384375 3.317901234567901 null HG00119 HG00119 GBR EUR false true 70.0 0.3195496417604913 3122 6648 1363 1365 394 2153 0 0 0 1743 410 7.527866752082009 1.7771483099316476 42.03939782190902 24.84769850706469 1759 4.251219512195122 3.464467005076142 null HG00120 HG00120 GBR EUR true true 68.0 0.28607983623336747 2795 6975 1238 1241 316 1873 0 0 0 1517 356 7.446153846153844 1.6802170140360537 41.18246869409654 23.966680366447953 1557 4.26123595505618 3.9272151898734178 null HG00128 HG00128 GBR EUR true true 67.0 0.6401228249744114 6254 3516 3277 2036 941 3918 0 0 0 3153 765 9.280620402942137 2.5949974996440823 45.32523185161495 27.475594538376384 2977 4.12156862745098 2.1636556854410203 null HG00131 HG00131 GBR EUR false false 72.0 0.309007164790174 3019 6751 1311 1317 391 2099 0 0 0 1712 387 7.452798940046386 1.6856292863721216 41.58860549850948 24.326264763553834 1708 4.423772609819121 3.368286445012788 null HG00138 HG00138 GBR EUR false false 74.0 0.2632548618219038 2572 7198 1042 1208 322 1852 0 0 0 1466 386 7.394245723172625 1.71175548989743 43.23911353032658 25.643111853445614 1530 3.7979274611398965 3.751552795031056 null HG00140 HG00140 GBR EUR false false 78.0 0.8098259979529171 7912 1858 4176 2473 1263 4999 0 0 0 4088 911 10.276921132457055 2.9365179618024126 47.77502527805855 27.51929083705252 3736 4.4873765093304065 1.958036421219319 null HG00141 HG00141 GBR EUR false false 77.0 0.9554759467758445 9335 435 5069 2712 1554 5820 0 0 1 4723 1097 12.910230316014964 3.6409086284306387 54.34933047670065 26.831973015992602 4266 4.3053783044667275 1.7451737451737452 null HG00150 HG00150 GBR EUR true true 64.0 0.1471852610030706 1438 8332 517 757 164 1085 0 0 0 892 193 7.117524339360223 1.715335880012245 44.71140472879002 25.97470194520383 921 4.6217616580310885 4.615853658536586 null HG00151 HG00151 GBR EUR false false 69.0 0.16407369498464688 1603 8167 655 758 190 1138 0 0 0 923 215 7.076107298814726 1.6005915370845802 41.79600748596385 24.751771954287438 948 4.293023255813954 3.9894736842105263 null HG00159 HG00159 GBR EUR false false 64.0 0.2202661207778915 2152 7618 919 964 269 1502 0 0 0 1206 296 7.2365241635687765 1.626426911510859 40.339684014869874 22.782883940441945 1233 4.074324324324325 3.58364312

In [43]:
display(sampleqc_table)

s sa_myAnnot_Sample sa_myAnnot_Population sa_myAnnot_SuperPopulation sa_myAnnot_isFemale sa_myAnnot_PurpleHair sa_myAnnot_CaffeineConsumption sa_qc_callRate sa_qc_nCalled sa_qc_nNotCalled sa_qc_nHomRef sa_qc_nHet sa_qc_nHomVar sa_qc_nSNP sa_qc_nInsertion sa_qc_nDeletion sa_qc_nSingleton sa_qc_nTransition sa_qc_nTransversion sa_qc_dpMean sa_qc_dpStDev sa_qc_gqMean sa_qc_gqStDev sa_qc_nNonRef sa_qc_rTiTv sa_qc_rHetHomVar sa_qc_rInsertionDeletion HG00096 HG00096 GBR EUR false false 77.0 0.2749232343909928 2686 7084 1130 1248 308 1864 0 0 1 1524 340 7.4586746090841425 1.8291623838959317 45.90655249441547 28.46876215640281 1556 4.482352941176471 4.0519480519480515 null HG00100 HG00100 GBR EUR true false 59.0 0.9616171954964176 9395 375 5081 2779 1535 5849 0 0 2 4762 1087 13.224374667376209 3.712169739189841 55.6111761575305 27.065478772644916 4314 4.380864765409384 1.8104234527687297 null HG00105 HG00105 GBR EUR false false 77.0 0.5797338792221085 5664 4106 2793 2024 847 3718 0 0 0 2993 725 8.650600282485852 2.2771253327175165 44.382591807909634 27.390137262730732 2871 4.128275862068966 2.3896103896103895 null HG00114 HG00114 GBR EUR false true 72.0 0.14943705220061412 1460 8310 509 776 175 1126 0 0 0 924 202 6.986301369863015 1.6055823053687388 43.37945205479454 25.086450301723687 951 4.574257425742574 4.434285714285714 null HG00115 HG00115 GBR EUR false true 71.0 0.6856704196519959 6699 3071 3479 2218 1002 4222 0 0 1 3451 771 9.22779519331246 2.5460202117218307 44.704433497536925 26.70956053033648 3220 4.476005188067445 2.2135728542914173 null HG00116 HG00116 GBR EUR false false 71.0 0.25220061412487205 2464 7306 1065 1075 324 1723 0 0 0 1403 320 7.394074675324675 1.7025517387131073 40.977678571428584 23.627226861323056 1399 4.384375 3.317901234567901 null HG00119 HG00119 GBR EUR false true 70.0 0.3195496417604913 3122 6648 1363 1365 394 2153 0 0 0 1743 410 7.527866752082009 1.7771483099316476 42.03939782190902 24.84769850706469 1759 4.251219512195122 3.464467005076142 null HG00120 HG00120 GBR EUR true true 68.0 0.28607983623336747 2795 6975 1238 1241 316 1873 0 0 0 1517 356 7.446153846153844 1.6802170140360537 41.18246869409654 23.966680366447953 1557 4.26123595505618 3.9272151898734178 null HG00128 HG00128 GBR EUR true true 67.0 0.6401228249744114 6254 3516 3277 2036 941 3918 0 0 0 3153 765 9.280620402942137 2.5949974996440823 45.32523185161495 27.475594538376384 2977 4.12156862745098 2.1636556854410203 null HG00131 HG00131 GBR EUR false false 72.0 0.309007164790174 3019 6751 1311 1317 391 2099 0 0 0 1712 387 7.452798940046386 1.6856292863721216 41.58860549850948 24.326264763553834 1708 4.423772609819121 3.368286445012788 null HG00138 HG00138 GBR EUR false false 74.0 0.2632548618219038 2572 7198 1042 1208 322 1852 0 0 0 1466 386 7.394245723172625 1.71175548989743 43.23911353032658 25.643111853445614 1530 3.7979274611398965 3.751552795031056 null HG00140 HG00140 GBR EUR false false 78.0 0.8098259979529171 7912 1858 4176 2473 1263 4999 0 0 0 4088 911 10.276921132457055 2.9365179618024126 47.77502527805855 27.51929083705252 3736 4.4873765093304065 1.958036421219319 null HG00141 HG00141 GBR EUR false false 77.0 0.9554759467758445 9335 435 5069 2712 1554 5820 0 0 1 4723 1097 12.910230316014964 3.6409086284306387 54.34933047670065 26.831973015992602 4266 4.3053783044667275 1.7451737451737452 null HG00150 HG00150 GBR EUR true true 64.0 0.1471852610030706 1438 8332 517 757 164 1085 0 0 0 892 193 7.117524339360223 1.715335880012245 44.71140472879002 25.97470194520383 921 4.6217616580310885 4.615853658536586 null HG00151 HG00151 GBR EUR false false 69.0 0.16407369498464688 1603 8167 655 758 190 1138 0 0 0 923 215 7.076107298814726 1.6005915370845802 41.79600748596385 24.751771954287438 948 4.293023255813954 3.9894736842105263 null HG00159 HG00159 GBR EUR false false 64.0 0.2202661207778915 2152 7618 919 964 269 1502 0 0 0 1206 296 7.2365241635687765 1.626426911510859 40.339684014869874 22.782883940441945 1233 4.074324324324325 3.58364312

In [44]:
vds_gDP_gGQ_vCR_sDP_sGT = (vds_gDP_gGQ_vCR
    .annotate_samples_vds(vds_gDP_gGQ_vCR, code = 'sa.qc = vds.qc' )
    .filter_samples_expr('sa.qc.dpMean > 0.50 && sa.qc.dpMean >=5 && sa.qc.gqMean >=20'))

As before, we can count the number of samples that remain in the dataset after filtering. (But nothing has been filtered out here)

In [46]:
vds_gDP_gGQ_vCR_sDP_sGT.count(genotypes=True)

Out[ 137 ]: {u'nGenotypes': 6936700L, u'nVariants': 9770L, u'nSamples': 710, u'nCalled': 3939258L, u'callRate': 56.78864589790535}

### Filter variants

We now have `vds_gDP_gGQ_vCR_sDP_sGT`, a VDS where low-quality genotypes and samples have been removed.

Let's use the [variant_qc](https://hail.is/hail/hail.VariantDataset.html#hail.VariantDataset.variant_qc) method to start exploring variant metrics:

In [48]:
vds_gDP_gGQ_vCR_sDP_sGT = vds_gDP_gGQ_vCR_sDP_sGT.split_multi()
vds_gDP_gGQ_vCR_sDP_sGT = vds_gDP_gGQ_vCR_sDP_sGT.variant_qc()
print(vds_gDP_gGQ_vCR_sDP_sGT.variant_schema)

Struct {
 rsid: String,
 qual: Double,
 filters: Set[String],
 pass: Boolean,
 info: Struct {
 AC: Array[Int],
 AF: Array[Double],
 AN: Int,
 BaseQRankSum: Double,
 ClippingRankSum: Double,
 DP: Int,
 DS: Boolean,
 FS: Double,
 HaplotypeScore: Double,
 InbreedingCoeff: Double,
 MLEAC: Array[Int],
 MLEAF: Array[Double],
 MQ: Double,
 MQ0: Int,
 MQRankSum: Double,
 QD: Double,
 ReadPosRankSum: Double,
 set: String
 },
 aIndex: Int,
 wasSplit: Boolean,
 qc: Struct {
 callRate: Double,
 AC: Int,
 AF: Double,
 nCalled: Int,
 nNotCalled: Int,
 nHomRef: Int,
 nHet: Int,
 nHomVar: Int,
 dpMean: Double,
 dpStDev: Double,
 gqMean: Double,
 gqStDev: Double,
 nNonRef: Int,
 rHeterozygosity: Double,
 rHetHomVar: Double,
 rExpectedHetFrequency: Double,
 pHWE: Double
 }
}

Next, we will filter variants following the [Best Practices GATK recommendations](https://gatkforums.broadinstitute.org/gatk/discussion/2806/howto-apply-hard-filters-to-a-call-set).

These recommendations are for human data, but our data is not human and the distribution of quality statistics will differ from expected for human. (Explain why it is so is beyond the scope of this tutorial.)

Let's have a look at the distribution of different variant quality statistics:

- QD - variant confidence standardized by depth.

  This annotation puts the variant confidence QUAL score into perspective by normalizing for the amount of coverage available. Because each read contributes a little to the QUAL score, variants in region with deep coverage can have artificially inflated QUAL scores, giving the impression that the call is supported by more evidence than it really is. To compensate for this, we normalize the variant confidence by depth, which gives us a more objective picture of how well supported the call is.
   
- MQ - Mapping quality of a SNP.

- FS - strand bias in support for REF vs ALT allele calls.

  Strand bias is a type of sequencing bias in which one DNA strand is favored over the other, which can result in incorrect evaluation of the amount of evidence observed for one allele vs. the other. The FisherStrand annotation is one of several methods that aims to evaluate whether there is strand bias in the data. It uses Fisher's Exact Test to determine if there is strand bias between forward and reverse strands for the reference or alternate allele. The output is a Phred-scaled p-value. The higher the output value, the more likely there is to be bias. More bias is indicative of false positive calls.
  
- SOR - sequencing bias in which one DNA strand is favored over the other
   
   Strand bias is a type of sequencing bias in which one DNA strand is favored over the other, which can result in incorrect evaluation of the amount of evidence observed for one allele vs. the other. It is used to determine if there is strand bias between forward and reverse strands for the reference or alternate allele. The reported value is ln-scaled.
   
- MQRankSum - Rank sum test for mapping qualities of REF vs. ALT reads.
   
   This variant-level annotation compares the mapping qualities of the reads supporting the reference allele with those supporting the alternate allele. The ideal result is a value close to zero, which indicates there is little to no difference. A negative value indicates that the reads supporting the alternate allele have lower mapping quality scores than those supporting the reference allele. Conversely, a positive value indicates that the reads supporting the alternate allele have higher mapping quality scores than those supporting the reference allele.

- ReadPosRankSum - do all the reads support a SNP call tend to be near the end of a read.
   
   The ideal result is a value close to zero, which indicates there is little to no difference in where the alleles are found relative to the ends of reads. A negative value indicates that the alternate allele is found at the ends of reads more often than the reference allele. Conversely, a positive value indicates that the reference allele is found at the ends of reads more often than the alternate allele.

We've once again used matplotlib to make histograms of these siz summary statistics.

In [51]:
variantqc_table = vds_gDP_gGQ_vCR_sDP_sGT.variants_keytable().to_dataframe()
display(variantqc_table)


v.contig v.start v.ref v.altAlleles va.rsid va.qual va.filters va.pass va.info.AC va.info.AF va.info.AN va.info.BaseQRankSum va.info.ClippingRankSum va.info.DP va.info.DS va.info.FS va.info.HaplotypeScore va.info.InbreedingCoeff va.info.MLEAC va.info.MLEAF va.info.MQ va.info.MQ0 va.info.MQRankSum va.info.QD va.info.ReadPosRankSum va.info.set va.aIndex va.wasSplit va.qc.callRate va.qc.AC va.qc.AF va.qc.nCalled va.qc.nNotCalled va.qc.nHomRef va.qc.nHet va.qc.nHomVar va.qc.dpMean va.qc.dpStDev va.qc.gqMean va.qc.gqStDev va.qc.nNonRef va.qc.rHeterozygosity va.qc.rHetHomVar va.qc.rExpectedHetFrequency va.qc.pHWE 1 904165 G List(List(G, A)) . 52346.37000000001 List() false List(518) List(0.103) 5020 -3.394 -0.17 17827 null 2.233 null 0.0988 List(514) List(0.102) 59.05 0 1.447 15.02 6.286 null 1 false 0.5098591549295775 96 0.13259668508287292 362 348 275 78 9 9.83425414364641 3.20912685351177 39.65469613259668 23.58784199754261 87 0.2154696132596685 8.666666666666666 0.23034776827674744 0.20903161534276152 1 1707740 T List(List(T, G)) . 93517.82 List() false List(997) List(0.198) 5034 -40.42 -0.287 19902 null 3.311 null 0.0387 List(983) List(0.195) 58.32 0 9.478 13.59 2.259 null 1 false 0.6211267605633802 189 0.21428571428571427 441 269 272 149 20 10.21315192743764 3.486925277157898 47.4965986394558 27.806353574108623 169 0.3378684807256236 7.45 0.3371169125993189 0.9436905368317897 1 2284195 T List(List(T, C)) . 142480.77 List() false List(1559) List(0.312) 4990 -45.982 0.35 18176 null 2.945 null 0.0925 List(1552) List(0.311) 58.57 0 16.136 15.48 -0.682 null 1 false 0.5633802816901409 268 0.335 400 310 176 180 44 10.092500000000006 3.8103731772623015 50.7575 28.513394988145485 224 0.45 4.090909090909091 0.446107634543179 0.8666508974008196 1 2944527 G List(List(G, A)) . 124329.15 List() false List(1206) List(0.245) 4928 0.063 -0.655 17698 null 0.449 null 0.1232 List(1192) List(0.242) 58.15 0 12.011 17.54 21.754 null 1 false 0.5253521126760563 194 0.26005361930294907 373 337 202 148 23 10.171581769436994 3.7226279911110978 49.97050938337803 28.09409102780986 171 0.3967828418230563 6.434782608695652 0.38536804793349766 0.5467951045957519 1 3761547 C List(List(C, A)) . 1614.69 List() false List(30) List(0.005948) 5044 -4.468 -8.82 16845 null 2.055 null -0.0047 List(28) List(0.005551) 56.98 0 6.299 7.99 -1.752 null 1 false 0.5464788732394367 11 0.014175257731958763 388 322 377 11 0 8.744845360824744 2.9197777818995676 35.706185567010316 14.995403518652447 11 0.028350515463917526 null 0.0279847023611573 0.534665074597403 1 3803755 T List(List(T, C)) . 383548.94 List() false List(3368) List(0.673) 5008 -53.782 -6.841 17687 null 9.582 null 0.0812 List(3376) List(0.674) 58.0 0 26.256 24.93 -0.433 null 1 false 0.5619718309859155 535 0.6704260651629073 399 311 41 181 177 9.28822055137844 3.3425391563162665 50.33834586466166 27.90654486651193 358 0.45363408521303256 1.0225988700564972 0.4424643792668623 0.6111203676316223 1 4121584 A List(List(A, G)) . 115117.70000000001 List() false List(1489) List(0.3) 4962 -26.975 -0.719 16179 null 22.674 null 0.104 List(1465) List(0.295) 58.55 0 2.845 14.32 -4.907 null 1 false 0.5408450704225352 229 0.2981770833333333 384 326 192 155 37 9.195312499999996 3.2557447474697825 49.64583333333334 27.71553008042402 192 0.4036458333333333 4.1891891891891895 0.4190806986093003 0.42986981696075716 1 4170048 C List(List(C, T)) . 120311.95 List() false List(1323) List(0.266) 4980 -12.472 -10.32 16375 null 4.365 null 0.1302 List(1313) List(0.264) 58.96 0 7.409 16.72 1.056 null 1 false 0.4859154929577465 180 0.2608695652173913 345 365 179 152 14 9.391304347826088 3.5403160069563744 48.275362318840585 27.32354935776841 166 0.4405797101449275 10.857142857142858 0.3861929702782861 0.006464828174270602 1 4180842 C List(List(C, T)) . 138252.12 List() false List(1429) List(0.286) 4996 54.319 -0.207 15845 null 0.321 null 0.0815 List(1430) List(0.286) 59.15 0 -1.479 17.99 -1.476 null 1 false 0.5098591549295775 228 0.31491712707

In [52]:
display(variantqc_table)display(variantqc_table)

v.contig v.start v.ref v.altAlleles va.rsid va.qual va.filters va.pass va.info.AC va.info.AF va.info.AN va.info.BaseQRankSum va.info.ClippingRankSum va.info.DP va.info.DS va.info.FS va.info.HaplotypeScore va.info.InbreedingCoeff va.info.MLEAC va.info.MLEAF va.info.MQ va.info.MQ0 va.info.MQRankSum va.info.QD va.info.ReadPosRankSum va.info.set va.aIndex va.wasSplit va.qc.callRate va.qc.AC va.qc.AF va.qc.nCalled va.qc.nNotCalled va.qc.nHomRef va.qc.nHet va.qc.nHomVar va.qc.dpMean va.qc.dpStDev va.qc.gqMean va.qc.gqStDev va.qc.nNonRef va.qc.rHeterozygosity va.qc.rHetHomVar va.qc.rExpectedHetFrequency va.qc.pHWE 1 904165 G List(List(G, A)) . 52346.37000000001 List() false List(518) List(0.103) 5020 -3.394 -0.17 17827 null 2.233 null 0.0988 List(514) List(0.102) 59.05 0 1.447 15.02 6.286 null 1 false 0.5098591549295775 96 0.13259668508287292 362 348 275 78 9 9.83425414364641 3.20912685351177 39.65469613259668 23.58784199754261 87 0.2154696132596685 8.666666666666666 0.23034776827674744 0.20903161534276152 1 1707740 T List(List(T, G)) . 93517.82 List() false List(997) List(0.198) 5034 -40.42 -0.287 19902 null 3.311 null 0.0387 List(983) List(0.195) 58.32 0 9.478 13.59 2.259 null 1 false 0.6211267605633802 189 0.21428571428571427 441 269 272 149 20 10.21315192743764 3.486925277157898 47.4965986394558 27.806353574108623 169 0.3378684807256236 7.45 0.3371169125993189 0.9436905368317897 1 2284195 T List(List(T, C)) . 142480.77 List() false List(1559) List(0.312) 4990 -45.982 0.35 18176 null 2.945 null 0.0925 List(1552) List(0.311) 58.57 0 16.136 15.48 -0.682 null 1 false 0.5633802816901409 268 0.335 400 310 176 180 44 10.092500000000006 3.8103731772623015 50.7575 28.513394988145485 224 0.45 4.090909090909091 0.446107634543179 0.8666508974008196 1 2944527 G List(List(G, A)) . 124329.15 List() false List(1206) List(0.245) 4928 0.063 -0.655 17698 null 0.449 null 0.1232 List(1192) List(0.242) 58.15 0 12.011 17.54 21.754 null 1 false 0.5253521126760563 194 0.26005361930294907 373 337 202 148 23 10.171581769436994 3.7226279911110978 49.97050938337803 28.09409102780986 171 0.3967828418230563 6.434782608695652 0.38536804793349766 0.5467951045957519 1 3761547 C List(List(C, A)) . 1614.69 List() false List(30) List(0.005948) 5044 -4.468 -8.82 16845 null 2.055 null -0.0047 List(28) List(0.005551) 56.98 0 6.299 7.99 -1.752 null 1 false 0.5464788732394367 11 0.014175257731958763 388 322 377 11 0 8.744845360824744 2.9197777818995676 35.706185567010316 14.995403518652447 11 0.028350515463917526 null 0.0279847023611573 0.534665074597403 1 3803755 T List(List(T, C)) . 383548.94 List() false List(3368) List(0.673) 5008 -53.782 -6.841 17687 null 9.582 null 0.0812 List(3376) List(0.674) 58.0 0 26.256 24.93 -0.433 null 1 false 0.5619718309859155 535 0.6704260651629073 399 311 41 181 177 9.28822055137844 3.3425391563162665 50.33834586466166 27.90654486651193 358 0.45363408521303256 1.0225988700564972 0.4424643792668623 0.6111203676316223 1 4121584 A List(List(A, G)) . 115117.70000000001 List() false List(1489) List(0.3) 4962 -26.975 -0.719 16179 null 22.674 null 0.104 List(1465) List(0.295) 58.55 0 2.845 14.32 -4.907 null 1 false 0.5408450704225352 229 0.2981770833333333 384 326 192 155 37 9.195312499999996 3.2557447474697825 49.64583333333334 27.71553008042402 192 0.4036458333333333 4.1891891891891895 0.4190806986093003 0.42986981696075716 1 4170048 C List(List(C, T)) . 120311.95 List() false List(1323) List(0.266) 4980 -12.472 -10.32 16375 null 4.365 null 0.1302 List(1313) List(0.264) 58.96 0 7.409 16.72 1.056 null 1 false 0.4859154929577465 180 0.2608695652173913 345 365 179 152 14 9.391304347826088 3.5403160069563744 48.275362318840585 27.32354935776841 166 0.4405797101449275 10.857142857142858 0.3861929702782861 0.006464828174270602 1 4180842 C List(List(C, T)) . 138252.12 List() false List(1429) List(0.286) 4996 54.319 -0.207 15845 null 0.321 null 0.0815 List(1430) List(0.286) 59.15 0 -1.479 17.99 -1.476 null 1 false 0.5098591549295775 228 0.31491712707

In [53]:
display(variantqc_table)

v.contig v.start v.ref v.altAlleles va.rsid va.qual va.filters va.pass va.info.AC va.info.AF va.info.AN va.info.BaseQRankSum va.info.ClippingRankSum va.info.DP va.info.DS va.info.FS va.info.HaplotypeScore va.info.InbreedingCoeff va.info.MLEAC va.info.MLEAF va.info.MQ va.info.MQ0 va.info.MQRankSum va.info.QD va.info.ReadPosRankSum va.info.set va.aIndex va.wasSplit va.qc.callRate va.qc.AC va.qc.AF va.qc.nCalled va.qc.nNotCalled va.qc.nHomRef va.qc.nHet va.qc.nHomVar va.qc.dpMean va.qc.dpStDev va.qc.gqMean va.qc.gqStDev va.qc.nNonRef va.qc.rHeterozygosity va.qc.rHetHomVar va.qc.rExpectedHetFrequency va.qc.pHWE 1 904165 G List(List(G, A)) . 52346.37000000001 List() false List(518) List(0.103) 5020 -3.394 -0.17 17827 null 2.233 null 0.0988 List(514) List(0.102) 59.05 0 1.447 15.02 6.286 null 1 false 0.5098591549295775 96 0.13259668508287292 362 348 275 78 9 9.83425414364641 3.20912685351177 39.65469613259668 23.58784199754261 87 0.2154696132596685 8.666666666666666 0.23034776827674744 0.20903161534276152 1 1707740 T List(List(T, G)) . 93517.82 List() false List(997) List(0.198) 5034 -40.42 -0.287 19902 null 3.311 null 0.0387 List(983) List(0.195) 58.32 0 9.478 13.59 2.259 null 1 false 0.6211267605633802 189 0.21428571428571427 441 269 272 149 20 10.21315192743764 3.486925277157898 47.4965986394558 27.806353574108623 169 0.3378684807256236 7.45 0.3371169125993189 0.9436905368317897 1 2284195 T List(List(T, C)) . 142480.77 List() false List(1559) List(0.312) 4990 -45.982 0.35 18176 null 2.945 null 0.0925 List(1552) List(0.311) 58.57 0 16.136 15.48 -0.682 null 1 false 0.5633802816901409 268 0.335 400 310 176 180 44 10.092500000000006 3.8103731772623015 50.7575 28.513394988145485 224 0.45 4.090909090909091 0.446107634543179 0.8666508974008196 1 2944527 G List(List(G, A)) . 124329.15 List() false List(1206) List(0.245) 4928 0.063 -0.655 17698 null 0.449 null 0.1232 List(1192) List(0.242) 58.15 0 12.011 17.54 21.754 null 1 false 0.5253521126760563 194 0.26005361930294907 373 337 202 148 23 10.171581769436994 3.7226279911110978 49.97050938337803 28.09409102780986 171 0.3967828418230563 6.434782608695652 0.38536804793349766 0.5467951045957519 1 3761547 C List(List(C, A)) . 1614.69 List() false List(30) List(0.005948) 5044 -4.468 -8.82 16845 null 2.055 null -0.0047 List(28) List(0.005551) 56.98 0 6.299 7.99 -1.752 null 1 false 0.5464788732394367 11 0.014175257731958763 388 322 377 11 0 8.744845360824744 2.9197777818995676 35.706185567010316 14.995403518652447 11 0.028350515463917526 null 0.0279847023611573 0.534665074597403 1 3803755 T List(List(T, C)) . 383548.94 List() false List(3368) List(0.673) 5008 -53.782 -6.841 17687 null 9.582 null 0.0812 List(3376) List(0.674) 58.0 0 26.256 24.93 -0.433 null 1 false 0.5619718309859155 535 0.6704260651629073 399 311 41 181 177 9.28822055137844 3.3425391563162665 50.33834586466166 27.90654486651193 358 0.45363408521303256 1.0225988700564972 0.4424643792668623 0.6111203676316223 1 4121584 A List(List(A, G)) . 115117.70000000001 List() false List(1489) List(0.3) 4962 -26.975 -0.719 16179 null 22.674 null 0.104 List(1465) List(0.295) 58.55 0 2.845 14.32 -4.907 null 1 false 0.5408450704225352 229 0.2981770833333333 384 326 192 155 37 9.195312499999996 3.2557447474697825 49.64583333333334 27.71553008042402 192 0.4036458333333333 4.1891891891891895 0.4190806986093003 0.42986981696075716 1 4170048 C List(List(C, T)) . 120311.95 List() false List(1323) List(0.266) 4980 -12.472 -10.32 16375 null 4.365 null 0.1302 List(1313) List(0.264) 58.96 0 7.409 16.72 1.056 null 1 false 0.4859154929577465 180 0.2608695652173913 345 365 179 152 14 9.391304347826088 3.5403160069563744 48.275362318840585 27.32354935776841 166 0.4405797101449275 10.857142857142858 0.3861929702782861 0.006464828174270602 1 4180842 C List(List(C, T)) . 138252.12 List() false List(1429) List(0.286) 4996 54.319 -0.207 15845 null 0.321 null 0.0815 List(1430) List(0.286) 59.15 0 -1.479 17.99 -1.476 null 1 false 0.5098591549295775 228 0.31491712707

In [54]:
display(variantqc_table)

v.contig v.start v.ref v.altAlleles va.rsid va.qual va.filters va.pass va.info.AC va.info.AF va.info.AN va.info.BaseQRankSum va.info.ClippingRankSum va.info.DP va.info.DS va.info.FS va.info.HaplotypeScore va.info.InbreedingCoeff va.info.MLEAC va.info.MLEAF va.info.MQ va.info.MQ0 va.info.MQRankSum va.info.QD va.info.ReadPosRankSum va.info.set va.aIndex va.wasSplit va.qc.callRate va.qc.AC va.qc.AF va.qc.nCalled va.qc.nNotCalled va.qc.nHomRef va.qc.nHet va.qc.nHomVar va.qc.dpMean va.qc.dpStDev va.qc.gqMean va.qc.gqStDev va.qc.nNonRef va.qc.rHeterozygosity va.qc.rHetHomVar va.qc.rExpectedHetFrequency va.qc.pHWE 1 904165 G List(List(G, A)) . 52346.37000000001 List() false List(518) List(0.103) 5020 -3.394 -0.17 17827 null 2.233 null 0.0988 List(514) List(0.102) 59.05 0 1.447 15.02 6.286 null 1 false 0.5098591549295775 96 0.13259668508287292 362 348 275 78 9 9.83425414364641 3.20912685351177 39.65469613259668 23.58784199754261 87 0.2154696132596685 8.666666666666666 0.23034776827674744 0.20903161534276152 1 1707740 T List(List(T, G)) . 93517.82 List() false List(997) List(0.198) 5034 -40.42 -0.287 19902 null 3.311 null 0.0387 List(983) List(0.195) 58.32 0 9.478 13.59 2.259 null 1 false 0.6211267605633802 189 0.21428571428571427 441 269 272 149 20 10.21315192743764 3.486925277157898 47.4965986394558 27.806353574108623 169 0.3378684807256236 7.45 0.3371169125993189 0.9436905368317897 1 2284195 T List(List(T, C)) . 142480.77 List() false List(1559) List(0.312) 4990 -45.982 0.35 18176 null 2.945 null 0.0925 List(1552) List(0.311) 58.57 0 16.136 15.48 -0.682 null 1 false 0.5633802816901409 268 0.335 400 310 176 180 44 10.092500000000006 3.8103731772623015 50.7575 28.513394988145485 224 0.45 4.090909090909091 0.446107634543179 0.8666508974008196 1 2944527 G List(List(G, A)) . 124329.15 List() false List(1206) List(0.245) 4928 0.063 -0.655 17698 null 0.449 null 0.1232 List(1192) List(0.242) 58.15 0 12.011 17.54 21.754 null 1 false 0.5253521126760563 194 0.26005361930294907 373 337 202 148 23 10.171581769436994 3.7226279911110978 49.97050938337803 28.09409102780986 171 0.3967828418230563 6.434782608695652 0.38536804793349766 0.5467951045957519 1 3761547 C List(List(C, A)) . 1614.69 List() false List(30) List(0.005948) 5044 -4.468 -8.82 16845 null 2.055 null -0.0047 List(28) List(0.005551) 56.98 0 6.299 7.99 -1.752 null 1 false 0.5464788732394367 11 0.014175257731958763 388 322 377 11 0 8.744845360824744 2.9197777818995676 35.706185567010316 14.995403518652447 11 0.028350515463917526 null 0.0279847023611573 0.534665074597403 1 3803755 T List(List(T, C)) . 383548.94 List() false List(3368) List(0.673) 5008 -53.782 -6.841 17687 null 9.582 null 0.0812 List(3376) List(0.674) 58.0 0 26.256 24.93 -0.433 null 1 false 0.5619718309859155 535 0.6704260651629073 399 311 41 181 177 9.28822055137844 3.3425391563162665 50.33834586466166 27.90654486651193 358 0.45363408521303256 1.0225988700564972 0.4424643792668623 0.6111203676316223 1 4121584 A List(List(A, G)) . 115117.70000000001 List() false List(1489) List(0.3) 4962 -26.975 -0.719 16179 null 22.674 null 0.104 List(1465) List(0.295) 58.55 0 2.845 14.32 -4.907 null 1 false 0.5408450704225352 229 0.2981770833333333 384 326 192 155 37 9.195312499999996 3.2557447474697825 49.64583333333334 27.71553008042402 192 0.4036458333333333 4.1891891891891895 0.4190806986093003 0.42986981696075716 1 4170048 C List(List(C, T)) . 120311.95 List() false List(1323) List(0.266) 4980 -12.472 -10.32 16375 null 4.365 null 0.1302 List(1313) List(0.264) 58.96 0 7.409 16.72 1.056 null 1 false 0.4859154929577465 180 0.2608695652173913 345 365 179 152 14 9.391304347826088 3.5403160069563744 48.275362318840585 27.32354935776841 166 0.4405797101449275 10.857142857142858 0.3861929702782861 0.006464828174270602 1 4180842 C List(List(C, T)) . 138252.12 List() false List(1429) List(0.286) 4996 54.319 -0.207 15845 null 0.321 null 0.0815 List(1430) List(0.286) 59.15 0 -1.479 17.99 -1.476 null 1 false 0.5098591549295775 228 0.31491712707

In [55]:
vds_gDP_gGQ_vCR_sDP_sGT_vFilter = vds_gDP_gGQ_vCR_sDP_sGT.filter_variants_expr('va.info.MQ >= 55.00 && va.info.QD >= 2.00 && va.info.FS <= 60.000 && va.info.MQRankSum >= -20.000 && va.info.ReadPosRankSum >= -10.000 && va.info.ReadPosRankSum <= 10.000')
print('variants before filtering: %d' % vds_gDP_gGQ_vCR_sDP_sGT.count_variants())
print('variants after filtering: %d' % vds_gDP_gGQ_vCR_sDP_sGT_vFilter.count_variants())

variants before filtering: 9770
variants after filtering: 9205

Verify the filtering results with plots:

In [57]:
variantqc_table = vds_gDP_gGQ_vCR_sDP_sGT_vFilter.variants_keytable().to_dataframe()

display(variantqc_table)

v.contig v.start v.ref v.altAlleles va.rsid va.qual va.filters va.pass va.info.AC va.info.AF va.info.AN va.info.BaseQRankSum va.info.ClippingRankSum va.info.DP va.info.DS va.info.FS va.info.HaplotypeScore va.info.InbreedingCoeff va.info.MLEAC va.info.MLEAF va.info.MQ va.info.MQ0 va.info.MQRankSum va.info.QD va.info.ReadPosRankSum va.info.set va.aIndex va.wasSplit va.qc.callRate va.qc.AC va.qc.AF va.qc.nCalled va.qc.nNotCalled va.qc.nHomRef va.qc.nHet va.qc.nHomVar va.qc.dpMean va.qc.dpStDev va.qc.gqMean va.qc.gqStDev va.qc.nNonRef va.qc.rHeterozygosity va.qc.rHetHomVar va.qc.rExpectedHetFrequency va.qc.pHWE 1 904165 G List(List(G, A)) . 52346.37000000001 List() false List(518) List(0.103) 5020 -3.394 -0.17 17827 null 2.233 null 0.0988 List(514) List(0.102) 59.05 0 1.447 15.02 6.286 null 1 false 0.5098591549295775 96 0.13259668508287292 362 348 275 78 9 9.83425414364641 3.20912685351177 39.65469613259668 23.58784199754261 87 0.2154696132596685 8.666666666666666 0.23034776827674744 0.20903161534276152 1 1707740 T List(List(T, G)) . 93517.82 List() false List(997) List(0.198) 5034 -40.42 -0.287 19902 null 3.311 null 0.0387 List(983) List(0.195) 58.32 0 9.478 13.59 2.259 null 1 false 0.6211267605633802 189 0.21428571428571427 441 269 272 149 20 10.21315192743764 3.486925277157898 47.4965986394558 27.806353574108623 169 0.3378684807256236 7.45 0.3371169125993189 0.9436905368317897 1 2284195 T List(List(T, C)) . 142480.77 List() false List(1559) List(0.312) 4990 -45.982 0.35 18176 null 2.945 null 0.0925 List(1552) List(0.311) 58.57 0 16.136 15.48 -0.682 null 1 false 0.5633802816901409 268 0.335 400 310 176 180 44 10.092500000000006 3.8103731772623015 50.7575 28.513394988145485 224 0.45 4.090909090909091 0.446107634543179 0.8666508974008196 1 3761547 C List(List(C, A)) . 1614.69 List() false List(30) List(0.005948) 5044 -4.468 -8.82 16845 null 2.055 null -0.0047 List(28) List(0.005551) 56.98 0 6.299 7.99 -1.752 null 1 false 0.5464788732394367 11 0.014175257731958763 388 322 377 11 0 8.744845360824744 2.9197777818995676 35.706185567010316 14.995403518652447 11 0.028350515463917526 null 0.0279847023611573 0.534665074597403 1 3803755 T List(List(T, C)) . 383548.94 List() false List(3368) List(0.673) 5008 -53.782 -6.841 17687 null 9.582 null 0.0812 List(3376) List(0.674) 58.0 0 26.256 24.93 -0.433 null 1 false 0.5619718309859155 535 0.6704260651629073 399 311 41 181 177 9.28822055137844 3.3425391563162665 50.33834586466166 27.90654486651193 358 0.45363408521303256 1.0225988700564972 0.4424643792668623 0.6111203676316223 1 4121584 A List(List(A, G)) . 115117.70000000001 List() false List(1489) List(0.3) 4962 -26.975 -0.719 16179 null 22.674 null 0.104 List(1465) List(0.295) 58.55 0 2.845 14.32 -4.907 null 1 false 0.5408450704225352 229 0.2981770833333333 384 326 192 155 37 9.195312499999996 3.2557447474697825 49.64583333333334 27.71553008042402 192 0.4036458333333333 4.1891891891891895 0.4190806986093003 0.42986981696075716 1 4170048 C List(List(C, T)) . 120311.95 List() false List(1323) List(0.266) 4980 -12.472 -10.32 16375 null 4.365 null 0.1302 List(1313) List(0.264) 58.96 0 7.409 16.72 1.056 null 1 false 0.4859154929577465 180 0.2608695652173913 345 365 179 152 14 9.391304347826088 3.5403160069563744 48.275362318840585 27.32354935776841 166 0.4405797101449275 10.857142857142858 0.3861929702782861 0.006464828174270602 1 4180842 C List(List(C, T)) . 138252.12 List() false List(1429) List(0.286) 4996 54.319 -0.207 15845 null 0.321 null 0.0815 List(1430) List(0.286) 59.15 0 -1.479 17.99 -1.476 null 1 false 0.5098591549295775 228 0.3149171270718232 362 348 159 178 25 8.674033149171263 2.8679674553362657 49.04143646408841 28.301376225885406 203 0.49171270718232046 7.12 0.4320854634235804 0.008798365893493797 1 6279383 G List(List(G, C)) . 1268.87 List() false List(16) List(0.003197) 5004 -4.319 -1.24 15942 null 3.279 null -0.028 List(15) List(0.002998) 58.22 0 0.258 10.75 1.466 null 1 false 0.43802816901408453 3 0.00482315112540193 311 399 

## PCA

To check if there is any genetic structure, we will use a principal component analysis (PCA).

In [59]:
vds_pca = (vds_gDP_gGQ_vCR_sDP_sGT_vFilter.pca(scores='sa.pca'))

In [60]:
type(vds_pca)

Out[ 69 ]: hail.dataset.VariantDataset

In [61]:
pca_table = vds_pca.samples_keytable().to_dataframe()
display(pca_table)

s sa.myAnnot.Sample sa.myAnnot.Population sa.myAnnot.SuperPopulation sa.myAnnot.isFemale sa.myAnnot.PurpleHair sa.myAnnot.CaffeineConsumption sa.qc.callRate sa.qc.nCalled sa.qc.nNotCalled sa.qc.nHomRef sa.qc.nHet sa.qc.nHomVar sa.qc.nSNP sa.qc.nInsertion sa.qc.nDeletion sa.qc.nSingleton sa.qc.nTransition sa.qc.nTransversion sa.qc.dpMean sa.qc.dpStDev sa.qc.gqMean sa.qc.gqStDev sa.qc.nNonRef sa.qc.rTiTv sa.qc.rHetHomVar sa.qc.rInsertionDeletion sa.pca.PC1 sa.pca.PC2 sa.pca.PC3 sa.pca.PC4 sa.pca.PC5 sa.pca.PC6 sa.pca.PC7 sa.pca.PC8 sa.pca.PC9 sa.pca.PC10 HG00096 HG00096 GBR EUR false false 77.0 0.2749232343909928 2686 7084 1130 1248 308 1864 0 0 1 1524 340 7.4586746090841425 1.8291623838959317 45.90655249441547 28.46876215640281 1556 4.482352941176471 4.0519480519480515 null -0.03259234728439644 -0.06855733119948931 -1.123812246816334E-4 0.028281177682584875 -0.014010634542255096 -0.017776752541682005 0.007053892909074455 0.02781819924015049 0.0022370033606121855 -2.0094674282807024E-4 HG00100 HG00100 GBR EUR true false 59.0 0.9616171954964176 9395 375 5081 2779 1535 5849 0 0 2 4762 1087 13.224374667376209 3.712169739189841 55.6111761575305 27.065478772644916 4314 4.380864765409384 1.8104234527687297 null -0.14113421655157857 -0.26957226301866216 0.015137134688259815 0.12393934258267862 0.037728080264608437 0.017008658210992494 -0.1158179938298054 -0.11662632686860075 0.10622958030085342 0.08420775565006634 HG00105 HG00105 GBR EUR false false 77.0 0.5797338792221085 5664 4106 2793 2024 847 3718 0 0 0 2993 725 8.650600282485852 2.2771253327175165 44.382591807909634 27.390137262730732 2871 4.128275862068966 2.3896103896103895 null -0.08684585592184543 -0.1365471331196452 0.018596742951730375 0.06115157920445044 -0.01954898933069777 -0.007632828645630781 0.0137735707058318 -0.012332066213168893 0.004046293374303001 0.0060683292505109366 HG00114 HG00114 GBR EUR false true 72.0 0.14943705220061412 1460 8310 509 776 175 1126 0 0 0 924 202 6.986301369863015 1.6055823053687388 43.37945205479454 25.086450301723687 951 4.574257425742574 4.434285714285714 null -0.015389097640296279 -0.03599863022512868 0.004691340853996382 0.017347060735838728 -0.008942582231820251 -0.007219581095956794 -0.0026005684325834675 0.006588598068711014 -5.640274308805656E-4 -0.0020790033670626544 HG00115 HG00115 GBR EUR false true 71.0 0.6856704196519959 6699 3071 3479 2218 1002 4222 0 0 1 3451 771 9.22779519331246 2.5460202117218307 44.704433497536925 26.70956053033648 3220 4.476005188067445 2.2135728542914173 null -0.08496850667940857 -0.1907138587745121 -4.6961778752089157E-4 0.040696982499270895 -0.005736134511733515 -0.004733120875151591 0.0014882309275965962 0.05229907038048517 -0.004633562020013328 -0.015235042281265581 HG00116 HG00116 GBR EUR false false 71.0 0.25220061412487205 2464 7306 1065 1075 324 1723 0 0 0 1403 320 7.394074675324675 1.7025517387131073 40.977678571428584 23.627226861323056 1399 4.384375 3.317901234567901 null -0.029027696477874967 -0.061609430700434925 0.0058841810945058325 0.017585679153929577 -0.0029524673108539626 -0.008161867408192372 0.00485891954111991 0.02033663355357532 -0.0029991626469734454 -0.002807222400257939 HG00119 HG00119 GBR EUR false true 70.0 0.3195496417604913 3122 6648 1363 1365 394 2153 0 0 0 1743 410 7.527866752082009 1.7771483099316476 42.03939782190902 24.84769850706469 1759 4.251219512195122 3.464467005076142 null -0.042700972224815295 -0.07347061478437117 6.949008546658025E-4 0.02549727455421067 -0.0047405508599820565 -0.014488921009977724 0.0010899562550298007 0.02255219093463539 0.003340051781761528 -0.005290501843283534 HG00120 HG00120 GBR EUR true true 68.0 0.28607983623336747 2795 6975 1238 1241 316 1873 0 0 0 1517 356 7.446153846153844 1.6802170140360537 41.18246869409654 23.966680366447953 1557 4.26123595505618 3.9272151898734178 null -0.03341728980047627 -0.07794578631497519 0.003522841996373467 0.030901953304205865 -0.006637890323862895 -0.009976241886953173 0.0020642819454803228 0.01355674423646

Install packages that are necessary to produce a geographic map:

## Summary:

Data filtering:
 - Filter genotypes
 - Filter samples
 - Filter variants

PCA -clustering of super-poupulations